## Organizing News and Sentiments into MySQL Database

For the convenience of analytics use cases, the news acrhives are absorbed into MySQL database:

* Read MySQL Creds
* Connect To MySQL Database
* Introduce Fields of Interest
* Creating Database Tables to Requirements
* Read, Parse and Archive Files
* Recurse and Gunzip News and Sentiment Scores
* Recurse and Insert News and Sentiment Scores

### Read MySQL Creds

In [1]:
import requests, json, time,  sys

credFile = open(".\creds\creds.txt","r")    # one per line
                                                #--- USER---
                                                #--- PASSWORD---
USERNAME = credFile.readline().rstrip('\n')
PASSWORD = credFile.readline().rstrip('\n')

credFile.close()

# Make sure that creds are read in correctly
#print("USERNAME="+str(USERNAME))
#print("PASSWORD="+str(PASSWORD))

### Connect To MySQL Db

In [2]:
import mysql.connector

DATABASE='newsanalyticsdb'
myConn = ""

try:
    myConn = mysql.connector.connect(
      host="localhost",
      user=USERNAME,
      passwd=PASSWORD,
      database=DATABASE
)
except mysql.connector.Error as err:
    if err.errno == errorcode.ER_ACCESS_DENIED_ERROR:
        print("Something is wrong with your user name or password")
    elif err.errno == errorcode.ER_BAD_DB_ERROR:
        print("Database does not exist")
    else:
        print(err)
        
else:
    print("Connected to "+ DATABASE)   
  

Connected to newsanalyticsdb


### Introduce Fields

In [3]:
# intorduce fields to archive from news
newsArchivedFields = {
    'id': 'VARCHAR(255)', 
    'feedTimestamp' : 'VARCHAR(255)',
    'emeaTimestamp' : 'VARCHAR(255)',
    'headline' : 'VARCHAR(520)',   #max is 512 + ...
    'subjects' : 'VARCHAR(10000)'}

# intorduce fields to archive from scores
scoresArchivedFields = {
    'id': 'VARCHAR(255)', 
    'assetId': 'VARCHAR(255)', 
    'assetName': 'VARCHAR(255)',
    'emeaTimestamp' : 'VARCHAR(255)',
    'sentimentNegative' : 'DECIMAL(10,6)',
    'sentimentNeutral' : 'DECIMAL(10,6)',
    'sentimentPositive' : 'DECIMAL(10,6)',
    'relevance' : 'DECIMAL(10,7)'}

### Define Create Table

In [5]:
def createTable(tableName, archivedFields):
    # concatenate fields into CREATE TABLE query
    CREATE_QUERY = 'CREATE TABLE ' + tableName + ' ('
    for k,v in archivedFields.items():
        CREATE_QUERY = CREATE_QUERY + str(k) + ' ' + str(v) + ','

    CREATE_QUERY = CREATE_QUERY + ' PRIMARY KEY ('+list(archivedFields.keys())[0]
    if list(archivedFields.keys())[1] == 'assetId':
        CREATE_QUERY = CREATE_QUERY +  ','+list(archivedFields.keys())[1]
    CREATE_QUERY = CREATE_QUERY +'))'
    print(CREATE_QUERY)

    #Get cursor to db connection 
    myCursor = myConn.cursor(buffered=True)

    #Droping table if exist 
    myCursor.execute("DROP TABLE IF EXISTS "+tableName) 

    #Creating NEWS table
    myCursor.execute(
        CREATE_QUERY)

    #myConn.close()
    
createTable('NEWS',newsArchivedFields)
createTable('SCORES', scoresArchivedFields)

CREATE TABLE NEWS (id VARCHAR(255),feedTimestamp VARCHAR(255),emeaTimestamp VARCHAR(255),headline VARCHAR(520),subjects VARCHAR(10000), PRIMARY KEY (id))
CREATE TABLE SCORES (id VARCHAR(255),assetId VARCHAR(255),assetName VARCHAR(255),emeaTimestamp VARCHAR(255),sentimentNegative DECIMAL(10,6),sentimentNeutral DECIMAL(10,6),sentimentPositive DECIMAL(10,6),relevance DECIMAL(10,7), PRIMARY KEY (id,assetId))


### Read, Parse and Archive Files

In [4]:
#NEWS_ARCHIVES_LOCATION = "c:\\docs\\ThomsonReuters\\NewsAnalytics\\TRNA_TRIAL\\Archives\\TR_News\\DOC\\EN\\Flat\\2YR\\"
NEWS_ARCHIVES_LOCATION = "c:\\docs\\ThomsonReuters\\NewsAnalytics\\TRNA_TRIAL\\Archives\\TR_News\\CMPNY_ALL\\EN\\Flat\\Historical\\"
NEWS_FILE_NAME = "TRNA.TR.News.CMPNY_ALL.EN.2018.40060097.Flat-News.txt"
SCORES_FILE_NAME = "TRNA.TR.News.CMPNY_ALL.EN.2018.40060097.Flat-Scores.txt"

def listToString(s):  
    strLst = ""   
    for elem in s:  
        strLst += elem   
    return strLst  

def readParseFile(fileNamePath, archivedFields, tableName):
    DEBUG_MAX_LINES = 5000000; i = 0; PRINT_STAT_EVERY = 10000;
    fieldPositions = archivedFields.copy();
    mySqlPart1 = "INSERT INTO "+tableName+ " (";
    mySqlPart2 = "";
    mySqlPart3 = "";
    
    #Get cursor to db connection 
    myCursor = myConn.cursor(buffered=True)
   
    with open(fileNamePath, encoding="utf8") as infile:
        for line in infile:
            mySqlPart3 = "";
            fields = line.split("\t")
            # from headers we obtain positions of fields to archive
            if i == 0:
                for j in range(len(fields)):
                    if fields[j] in archivedFields:
                        fieldPositions[fields[j]] = j; 
                print('Table '+tableName +' Field Positions:')
                print(fieldPositions)
                for key in fieldPositions.keys():
                   mySqlPart2 = mySqlPart2 + key + "," 
                mySqlPart2 = mySqlPart2[:len(mySqlPart2)-1] + ') VALUES ('
            # from each next line we derive values that populate mySql inserts
            else:
#                print("Line "+str(i) + "# of lenth " + str(len(fields))+ ":")
#                print(fields)
  #              if 'Flat-News' in fileNamePath and i > 982139:
  #                  print(i)
  #                  print(fields)
                for key in fieldPositions.keys():
                    try:
                        if fieldPositions[key] <= len(fields):
                            mySqlPart3 = mySqlPart3 + "\'" + fields[fieldPositions[key]].replace("'", r"\'") + "\' ," 
                        else: 
                            print("Fields too short: " + fields)
                            mySqlPart3 = mySqlPart3 + "\'NULL\' ,"
                    except:
                        print("Exception on" + listToString(fields) + " retrieving "+key)
                mySqlPart3 = mySqlPart3[:len(mySqlPart3)-1] + ')'
                # concatenate INSERT and execute it 
#                print("Executing :"+mySqlPart1 + mySqlPart2 + mySqlPart3)
                try :
                    myCursor.execute(mySqlPart1 + mySqlPart2 + mySqlPart3)
                except mysql.connector.Error as error:
                    print( "*** Failed to execute {} error {} ".format(mySqlPart1 + mySqlPart2 + mySqlPart3, error))
            i = i + 1;
            if i % PRINT_STAT_EVERY == 0:
                print("Inserted "+ str(i) + " lines")
                myConn.commit()
            if DEBUG_MAX_LINES > 0 and i == DEBUG_MAX_LINES:
                break;
                
        myConn.commit()
        print("******************End of readParseFile, lines "+ str(i)) 

readParseFile(NEWS_ARCHIVES_LOCATION + SCORES_FILE_NAME, scoresArchivedFields, 'SCORES')
#readParseFile(NEWS_ARCHIVES_LOCATION + NEWS_FILE_NAME, newsArchivedFields, 'NEWS')

### Recurse and Gunzip News and Sentiment Scores
(done once)

In [5]:
import os
import sys
import gzip
import shutil
import fnmatch

DIR2020 = 'C:\\docs\\ThomsonReuters\\NewsAnalytics\\TRNA_TRIAL\\Archives\\TR_News\\CMPNY_ALL\\EN\\Flat\\Historical\\v41\\2020'


def listFiles(startpath):
    for root,d_names,f_names in os.walk(DIR2020):
        for f in f_names:
            print(os.path.join(root, f))
            if file.find('.gz') != -1:
                print('GZIP')
#listFiles(DIR2020)

def gunzip(file_path,output_path):
    with gzip.open(file_path,"rb") as f_in, open(output_path,"wb") as f_out:
        shutil.copyfileobj(f_in, f_out)

def recurseGunzip(root):
    walker = os.walk(root)
    for root,dirs,files in walker:
        for f in files:
            if fnmatch.fnmatch(f,"*.gz"):
                print(os.path.join(root, f))
                gunzip(os.path.join(root, f),os.path.join(root, f).replace(".gz",""))

recurseGunzip(DIR2020)               
                

C:\docs\ThomsonReuters\NewsAnalytics\TRNA_TRIAL\Archives\TR_News\CMPNY_ALL\EN\Flat\Historical\v41\2020\01\01\NA_ENT0.TR.News.CMPNY_ALL.EN.2020-01-01_00.41030111.Flat-News.txt.gz
C:\docs\ThomsonReuters\NewsAnalytics\TRNA_TRIAL\Archives\TR_News\CMPNY_ALL\EN\Flat\Historical\v41\2020\01\01\NA_ENT0.TR.News.CMPNY_ALL.EN.2020-01-01_00.41030111.Flat-Scores.txt.gz
C:\docs\ThomsonReuters\NewsAnalytics\TRNA_TRIAL\Archives\TR_News\CMPNY_ALL\EN\Flat\Historical\v41\2020\01\01\NA_ENT0.TR.News.CMPNY_ALL.EN.2020-01-01_01.41030111.Flat-News.txt.gz
C:\docs\ThomsonReuters\NewsAnalytics\TRNA_TRIAL\Archives\TR_News\CMPNY_ALL\EN\Flat\Historical\v41\2020\01\01\NA_ENT0.TR.News.CMPNY_ALL.EN.2020-01-01_01.41030111.Flat-Scores.txt.gz
C:\docs\ThomsonReuters\NewsAnalytics\TRNA_TRIAL\Archives\TR_News\CMPNY_ALL\EN\Flat\Historical\v41\2020\01\01\NA_ENT0.TR.News.CMPNY_ALL.EN.2020-01-01_02.41030111.Flat-News.txt.gz
C:\docs\ThomsonReuters\NewsAnalytics\TRNA_TRIAL\Archives\TR_News\CMPNY_ALL\EN\Flat\Historical\v41\2020\01\

### Recurse and Insert News and Sentiment Scores

In [6]:
def recurseDbInsert(root):
    walker = os.walk(root)
    for root,dirs,files in walker:
        for f in files:
            if fnmatch.fnmatch(f,"*-News.txt"):
                print("Inserting NEWS:"+os.path.join(root, f))
                readParseFile(os.path.join(root, f), newsArchivedFields, 'NEWS')
            elif fnmatch.fnmatch(f,"*-Scores.txt"):
                print("Inserting SCORES:"+os.path.join(root, f))
                readParseFile(os.path.join(root, f), scoresArchivedFields, 'SCORES')

#recurseDbInsert(DIR2020) 

# insert additional available archived folders
DIR2020_11 = 'C:\\docs\\ThomsonReuters\\NewsAnalytics\\TRNA_TRIAL\\Archives\\TR_News\\CMPNY_ALL\\EN\\Flat\\Historical\\v41\\2020\\11'
recurseDbInsert(DIR2020_11)
DIR2020_12 = 'C:\\docs\\ThomsonReuters\\NewsAnalytics\\TRNA_TRIAL\\Archives\\TR_News\\CMPNY_ALL\\EN\\Flat\\Historical\\v41\\2020\\12'
recurseDbInsert(DIR2020_12)


Inserting NEWS:C:\docs\ThomsonReuters\NewsAnalytics\TRNA_TRIAL\Archives\TR_News\CMPNY_ALL\EN\Flat\Historical\v41\2020\11\01\NA_ENT0.TR.News.CMPNY_ALL.EN.2020-11-01_00.41030120.Flat-News.txt
Table NEWS Field Positions:
{'id': 3, 'feedTimestamp': 9, 'emeaTimestamp': 2, 'headline': 6, 'subjects': 18}
******************End of readParseFile, lines 4
Inserting SCORES:C:\docs\ThomsonReuters\NewsAnalytics\TRNA_TRIAL\Archives\TR_News\CMPNY_ALL\EN\Flat\Historical\v41\2020\11\01\NA_ENT0.TR.News.CMPNY_ALL.EN.2020-11-01_00.41030120.Flat-Scores.txt
Table SCORES Field Positions:
{'id': 3, 'assetId': 6, 'assetName': 7, 'emeaTimestamp': 2, 'sentimentNegative': 13, 'sentimentNeutral': 14, 'sentimentPositive': 15, 'relevance': 11}
******************End of readParseFile, lines 6
Inserting NEWS:C:\docs\ThomsonReuters\NewsAnalytics\TRNA_TRIAL\Archives\TR_News\CMPNY_ALL\EN\Flat\Historical\v41\2020\11\01\NA_ENT0.TR.News.CMPNY_ALL.EN.2020-11-01_01.41030120.Flat-News.txt
Table NEWS Field Positions:
{'id': 3, 'f